In [1]:
import base64
import json
import pandas as pd
from PIL import Image
import folium
from folium import Map, GeoJson, Choropleth, Marker, CircleMarker, TileLayer, GeoJsonTooltip, Tooltip, Popup, Icon, IFrame, Html, FeatureGroup

In [2]:
df = pd.read_excel('MT Base consolidada.xlsx')
with open('Casanare_municipios.geojson', encoding="utf8") as f:
    casanare_mapa = json.loads(f.read())

In [3]:
basemaps = {
    'Google Satellite': TileLayer(
        tiles = 'https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',
        attr = 'Google',
        name = 'Google Satellite',
        overlay = False,
        control = True,
        show=True
    ),
    'Google Terrain': TileLayer(
        tiles = 'https://mt1.google.com/vt/lyrs=p&x={x}&y={y}&z={z}',
        attr = 'Google',
        name = 'Google Terrain',
        overlay = False,
        control = True,
        show=False
    )
}

In [9]:
df = df[(df['Presencia_trypanosoma'] == 1) & (df['Organismos'] == 'Murcielago')]
df_resumen = df.groupby(['Sitio_de_colecta', 'W', 'N', 'Especie_12S']).agg({'Nombre muestra': 'count'}).reset_index().rename(columns={'N': 'Latitud', 'W': 'Longitud', 'Especie_12S': 'Especie', 'Nombre muestra': 'Cantidad'})
df_resumen = df_resumen[df_resumen['Cantidad'] != 0]
df_resumen

Sitio_de_colecta   Longitud   Latitud                   Especie  \
0             Belgrado (Maní) -72.337748  4.816131           Myotis brandtii   
1         Cruz Verde (Tamara) -72.100201  5.482160    Carollia perspicillata   
2         Cruz Verde (Tamara) -72.100201  5.482160      Glossophaga soricina   
3   Cueva guacharos (Aguazul) -72.576252  5.208503    Carollia perspicillata   
4   Cueva guacharos (Aguazul) -72.576252  5.208503      Glossophaga soricina   
5   Cueva guacharos (Aguazul) -72.576252  5.208503  Micronycteris brachyotis   
6               Curama (pore) -72.040339  5.703134           Myotis brandtii   
7               Curama (pore) -72.040339  5.703134     Phyllostomus hastatus   
8               Curama (pore) -72.040339  5.703134       Saccopteryx leptura   
9       La Graciela (Aguazul) -72.459936  4.872883    Carollia perspicillata   
10      La Graciela (Aguazul) -72.459936  4.872883  Micronycteris brachyotis   
11           La niata (yopal) -72.309545  5.407267       Carollia brevicauda   
12           La niata (yopal) -72.309545  5.407267    Carollia perspicillata   
13           La niata (yopal) -72.309545  5.407267     Phyllostomus hastatus   
14           La niata (yopal) -72.309545  5.407267         Vampyrum spectrum   
15        Ramon Nonato (Pore) -72.088302  5.667533       Saccopteryx leptura   
16          San Isidro (Pore) -72.053535  5.658318           Anoura caudifer   
17          San Isidro (Pore) -72.053535  5.658318    Carollia perspicillata   
18          San Isidro (Pore) -72.053535  5.658318      Glossophaga soricina   
19          San Isidro (Pore) -72.053535  5.658318           Myotis brandtii   
20          San Isidro (Pore) -72.053535  5.658318     Phyllostomus hastatus   

    Cantidad  
0          5  
1          5  
2          4  
3          8  
4          1  
5          1  
6          1  
7          1  
8          2  
9          6  
10         1  
11         1  
12         2  
13        11  
14         1  
15         1  
16         1  
17         3  
18         3  
19         2  
20         3

In [71]:
df_resumen.Especie.unique()

array(['Carollia perspicillata', 'Glossophaga soricina',
       'Micronycteris brachyotis', 'Myotis brandtii',
       'Phyllostomus hastatus', 'Anoura caudifer', 'Saccopteryx leptura'],
      dtype=object)

In [16]:
color_especie = {'Carollia perspicillata': '#b2df8a', 'Glossophaga soricina': '#33a02c', 'Micronycteris brachyotis': '#fb9a99', 'Myotis brandtii': '#e31a1c',
                 'Phyllostomus hastatus': '#fdbf6f', 'Anoura caudifer': '#a6cee3', 'Saccopteryx leptura': '#ff7f00', 'Carollia brevicauda': '#1f78b4',
                'Vampyrum spectrum': '#cab2d6'}

hospedero_map = Map(location=[5.190831, -72.322258], tiles=None, zoom_start=9)
style = {'fillColor': '#00FFFFFF', 'lineColor': '#000000', "weight": 5}
GeoJson(casanare_mapa, name = 'Municipios de Casanare', overlay = True, style_function=lambda x: style, tooltip=GeoJsonTooltip(fields=['MPIO_CNMBR'], aliases=['MUNICIPIO'])).add_to(hospedero_map)

for especie in df_resumen.Especie.unique():
    temp_df = df_resumen[df_resumen['Especie'] == especie]
    show_especie = True if especie == 'Carollia perspicillata' else False
    feature_group = FeatureGroup(especie, show=show_especie)
    
    html_tooltip = """
    <h4><i>{}</i></h4>
    <h5><b>Cantidad:</b> {}</h5>
    """.format
    
    temp_df.apply(lambda row: feature_group.add_child(CircleMarker([row['Latitud'], row['Longitud']], radius=5*row['Cantidad'], tooltip=Tooltip(html_tooltip(especie, row['Cantidad'])), color=color_especie[especie], fill=True)), axis=1)
    feature_group.add_to(hospedero_map)    
    
basemaps['Google Satellite'].add_to(hospedero_map)
basemaps['Google Terrain'].add_to(hospedero_map)
# TileLayer('Stamen Terrain', name='Stamen Terrain', overlay=False, show=False).add_to(hospedero_map)

folium.LayerControl().add_to(hospedero_map)
hospedero_map